In [1]:
import ROOT
import stage1
import utils
import histogram_manager as hm

%jsroot on

Welcome to JupyROOT 6.28/00


In [2]:
# Nbins = 100000
# down = 0
# up =100000

down = 0
up =1000000
Nbins = 100000

xbins_En = utils.get_xbins_En_10ns(Nbins, down, up, 21.5)

In [7]:
c = ROOT.TCanvas()
cross_section = stage1.get_cross_section(stage1.CROSS_SECTION_PATH, xbins_En)
cross_section.Draw()
cross_section.GetXaxis().SetRangeUser(3,100)
c.Draw()

Warning in <TROOT::Append>: Replacing existing TH1: hEn_sig_tot_10Bo (Potential memory leak).


In [4]:
# hists_Bo = hm.HistogramManager(stage1.BORON_PATH)
# hEn_all_gate_Bo = hists_Bo.get("hEn_all_gate_Bo")
# # hEn_all_gate_Bo.Draw()

n = 1.41E23 # number density of 10Co[atom/cm^3]
d = 0.1 # target thickness [cm]
f = 1E-24


divisor = cross_section.Clone()

for bin in range(1, divisor.GetNbinsX() + 1):  # Remember bin indices start from 1 in ROOT
    original_value = divisor.GetBinContent(bin)
    divisor.SetBinContent(bin, (1 - ROOT.TMath.Exp(-1 * n * d * f * original_value)))


c = ROOT.TCanvas()
# cross_section.Draw("same")
divisor.Draw()
c.Draw()

In [5]:
# beam_intensity = stage1.get_beam_intensity(stage1.BORON_PATH, cross_section)
beam_intensity = stage1.get_beam_intensity(stage1.BORON_PATH, divisor)


c = ROOT.TCanvas()
beam_intensity.Draw()
beam_intensity.GetXaxis().SetRange(1,90000)
beam_intensity.SetName("hEn_beam_intensity")
beam_intensity.SetTitle("hEn_beam_intensity")
beam_intensity.GetYaxis().SetTitle("Intensity [A.U.]")

# print(beam_intensity.GetNbinsX())
# print(beam_intensity.GetXaxis().GetLast())
# print(beam_intensity.GetXaxis().GetFirst())
# print(beam_intensity.GetXaxis().GetXbins())
# xbins = beam_intensity.GetXaxis().GetXbins()
# print([xbins[0]])

c.Draw()

In [7]:
# hEn_zero = utils.get_hist(stage1.INPUT_PATH, "hEn_zero_d1")
# hEn = utils.get_hist(stage1.INPUT_PATH, "hEn_d1")
# hEn_gtzero = utils.get_hist(stage1.INPUT_PATH, "hEn_gtzero_d1")
# hEn_pu = utils.get_hist(stage1.INPUT_PATH, "hEn_pu_d1")
# hEn_npu = utils.get_hist(stage1.INPUT_PATH, "hEn_npu_d1")
# hEn_npu_gtzero = utils.get_hist(stage1.INPUT_PATH, "hEn_npu_gtzero_d1")

# pu_corr1 = stage1.calc_purate1(hEn_zero,hEn_gtzero)
# pu_corr2 = stage1.calc_purate2(hEn_pu,hEn_npu)

# pu_rate1 = hEn_gtzero * pu_corr1
# pu_rate2 = hEn_npu_gtzero * pu_corr2

# pu_rate1.Draw()
# pu_rate1.GetXaxis().SetRange(1,90000)
# pu_rate2.Draw("same")

# pu_rate2.SetLineColor(ROOT.kRed)

# leg = ROOT.TLegend(.73,.32,.97,.53)
# leg.AddEntry(pu_rate1,"PU FLAG method","L")
# leg.AddEntry(pu_rate2,"PH=0 method","L")
# leg.Draw()

# ROOT.gROOT.GetListOfCanvases().Draw()

In [8]:
# def get_pu_corr_dict(gtzero_dict, zero_dict):
#     """"""
#     # TODO: Find better way to get the correct key names
#     pu_corr_dict = {}
    
#     for key, hist in gtzero_dict["hEn_gtzero"].items():
#         for key1, hist1 in zero_dict["hEn_zero"].items():
#             if utils.same_channel(key,key1):
#                 pu_corr_dict[f"pucorr_d{key[-1]}"] = calc_purate1(hist1,hist)
                
#     return pu_corr_dict
    

In [9]:
# # hist_dict = utils.read_root_to_dict("../output/stage0_output.root")


# hEn_gtzero_dict = utils.get_from_dict(hist_dict, "hEn_gtzero")
# hEn_zero_dict = utils.get_from_dict(hist_dict, "hEn_zero")

# pu_corr_dict = stage1.get_pu_corr_dict(hEn_gtzero_dict, hEn_zero_dict)
    


In [12]:
hist_dict = utils.read_root_to_dict(stage1.INPUT_PATH)

hEn_gtzero_dict = utils.get_from_dict(hist_dict, "hEn_gtzero")
hEn_zero_dict = utils.get_from_dict(hist_dict, "hEn_zero")
pu_corr_dict = stage1.get_pu_corr_dict(hEn_gtzero_dict, hEn_zero_dict)

hEgam_dict = utils.get_from_dict(hist_dict,"hEgam")
hEn_gate_bkg_dict = utils.get_from_dict(hist_dict,"hEn_gatebkg")
bkg_dict = stage1.get_bkg_dict(hEgam_dict,hEn_gate_bkg_dict,[5134,5164],[4980,5050],[5200,5600])
# print(bkg_dict["bkg_d1"])

# hist_dict = stage1.apply_correction(hist_dict, stage1.beam_correction, "beamcorr", "hEn", beam_intensity)
hist_dict = stage1.apply_corrections(hist_dict, stage1.pu_correction, "pucorr", "hEn", pu_corr_dict)
hist_dict = stage1.apply_corrections(hist_dict, stage1.bkg_subtraction, "bkgsub", "hEn_gate", bkg_dict)

hist_dict = utils.sort_dict_by_type_and_key(hist_dict)
utils.write_dict_to_root(hist_dict,stage1.OUTPUT_PATH)
# hist_dict

Applying pucorr to hEn_zero_d0 using pucorr_d0
Applying pucorr to hEn_zero_d1 using pucorr_d1
Applying pucorr to hEn_zero_d2 using pucorr_d2
Applying pucorr to hEn_zero_d3 using pucorr_d3
Applying pucorr to hEn_zero_d4 using pucorr_d4
Applying pucorr to hEn_zero_d5 using pucorr_d5
Applying pucorr to hEn_zero_d6 using pucorr_d6
Applying pucorr to hEn_zero_d7 using pucorr_d7
Applying pucorr to hEn_zero_d8 using pucorr_d8
Applying pucorr to hEn_zero_d9 using pucorr_d9
Applying pucorr to hEn_zero_d10 using pucorr_d10
Applying pucorr to hEn_zero_d11 using pucorr_d11
Applying pucorr to hEn_zero_d12 using pucorr_d12
Applying pucorr to hEn_zero_d13 using pucorr_d13
Applying pucorr to hEn_zero_d14 using pucorr_d14
Applying pucorr to hEn_zero_d15 using pucorr_d15
Applying pucorr to hEn_zero_d16 using pucorr_d16
Applying pucorr to hEn_zero_d17 using pucorr_d17
Applying pucorr to hEn_zero_d18 using pucorr_d18
Applying pucorr to hEn_zero_d19 using pucorr_d19
Applying pucorr to hEn_zero_d20 using pu

In [ ]:
# hist = utils.get_hist("../output/stage1_output.root","hEn_beamcorr_pucorr_d1")
# hist.Rebin(10)
# hist.GetXaxis().SetRangeUser(5,500)




# hist.Draw()
# hist_bkg = hist.ShowBackground(40,"nocompton")
# hist_sub = hist - hist_bkg
# hist_bkg.Draw("same")
# hist_sub.Draw("same")
# hist_sub.SetLineColor(ROOT.kRed)
# ROOT.gROOT.GetListOfCanvases().Draw()